<img src="https://avatars.githubusercontent.com/u/74911464?s=200&v=4"
     alt="OpenEO Platform logo"
     style="float: left; margin-right: 10px;" />
# openEO Platform - Analysis Ready Data

#### First steps using openEO within the Copernicus DataSpace

Make sure that the required libraries are available to run this notebook

Import the required python sitepackages

In [ ]:
!pip install --upgrade openeo

In [ ]:
#copy required libraries
!cp /home/jovyan/mystorage/EENSAT/software/lib* /home/jovyan/.local/lib/

In [ ]:
#load all required libraries
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

In [ ]:
pip install /home/jovyan/mystorage/EENSAT/software/ilwis-1.0.20230718-cp311-cp311-linux_x86_64.whl

In [ ]:
#copy some other required software tools - ffmpeg is used for animations
#ffmpeg and ffprobe is assumed to be available in the notebook folder /software
#files are copied into a selected folder given within the currently configured directories in $PATH (in the notebook environment)
!cp /home/jovyan/mystorage/EENSAT/software/ffmpeg /opt/conda/bin
!cp /home/jovyan/mystorage/EENSAT/software/ffprobe /opt/conda/bin

In [ ]:
import ilwis
import openeo
import os
import numpy as np
from matplotlib import pyplot as plt

Check the ILWISPy version used within this notebook

In [ ]:
ilwis.version()

Create within your notebook directory a folder to store your downloaded / processed results 

In [ ]:
!mkdir -p data

Assign the created folder as your ILWISPy working directory

In [ ]:
work_dir = os.getcwd() + '/data'

#set the working directory for ILWISPy
ilwis.setWorkingCatalog(work_dir)
print(work_dir)

Review some of the documentation available on openEO, see the 
reference at: https://open-eo.github.io/openeo-python-client/

In [ ]:
print(openeo.client_version())

In [ ]:
#remove any existing authentication
!rm -rf /home/eoafrica/.local/share/openeo-python-client/refresh-tokens.json

Establish the connection the the Copernicus Data Space

In [ ]:
connection = openeo.connect("openeo.dataspace.copernicus.eu").authenticate_oidc()

Get a listing of currently available collections

In [ ]:
print(connection.list_collection_ids())

Image selection from Sentinel-2, level 2 of a number of spectral channels, over a given time range for a given area of interest (aoi), using a maximum cloud cover threshold

In [ ]:
aoi = {'west': 6.8375, 'east': 6.8899, 'south': 52.21168, 'north': 52.2411,"crs": "EPSG:4326",} #  Enschede_North East, centred around harbour and Utwente
t = ["2023-05-01", "2023-06-30"]
s2_cube = connection.load_collection("SENTINEL2_L2A",
    spatial_extent= aoi,
    temporal_extent= t,
    bands=['B02', 'B03', 'B04', "B08"],
    max_cloud_cover=1,
)

Perform a temporal reduction, using the median value for each pixel within your data stack

In [ ]:
s2_cube_red = s2_cube.median_time()

Store your results obtained

In [ ]:
s2_cube_red.download("./data/Enschede.tif")

Use ILWISPy for visualization and processing of the downloaded image, first the image is loaded

In [ ]:
raster = ilwis.RasterCoverage ('Enschede.tif')
print(raster.size())

From the image select and assign the spectral bands as seperate variables

In [ ]:
#note index starts from 0
Blue = ilwis.do('selection',raster,"rasterbands(0)")
Green = ilwis.do('selection',raster,"rasterbands(1)")
Red = ilwis.do('selection',raster,"rasterbands(2)")
IR = ilwis.do('selection',raster,"rasterbands(3)")
print(IR.size().xsize)
print(IR.size().ysize)
print(IR.size().zsize)

Calculate images statistics, here the near infrared (IR) cpectral channel is used

In [ ]:
stats = Blue.statistics(ilwis.PropertySets.pHISTOGRAM)
print(stats.histogram())

Display some of the image statistical parameters obtained

In [ ]:
print(stats[ilwis.PropertySets.pMIN]) # minimum value on the map
print(stats[ilwis.PropertySets.pMAX]) # maximum value on the map
print(stats[ilwis.PropertySets.pMEAN]) # average value, excluding undefs - nodata
print(stats[ilwis.PropertySets.pCOUNT]) # total number of pixels including undefs - nodata
print(stats[ilwis.PropertySets.pNETTOCOUNT]) # total number of pixels excluding undefs - nodata
print(stats[ilwis.PropertySets.pSUM]) # sum of all values, excluding undefs - nodata

Create a histogram plot (using Matplotlib) of the IR channel - note the data range!

In [ ]:
x=[a for (a,b) in stats.histogram()][:-1] #don't plot the last tuple
y=[b for (a,b) in stats.histogram()][:-1] #don't plot the last tuple

plt.plot(x,y,label='Raster values')
plt.xlabel('Data Range')
plt.ylabel('Frequency')
plt.title('Histogram')
plt.legend()

Conduct some further image processing for each of the spectral channels, calculation the histogram (now using a large number of bins), conducting a linear stretch omitting the lower and upper tail of the histogram (1 % cut-off) and assigning the stretched data to a data range from 0 to 255, whole numbers only (precision is set to 1)

In [ ]:
# calculate statistics, retrieve cut-off at lower and upper tail of 1%, conduct linear stretch and ensure that all data is transformed to a byte range
# note that this can also be done in a loop, but here each band is handled seperately
stat_Blue = Blue.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_Blue.calcStretchRange(1)
Blues = ilwis.do('linearstretch',Blue, minPerc1, maxPerc1)
Blues = ilwis.do('setvaluerange', Blues, 0, 255, 1)
print()
print(minPerc1)
print(maxPerc1)
stat_Green = Green.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_Green.calcStretchRange(1)
Greens = ilwis.do('linearstretch',Green, minPerc1, maxPerc1)
Greens = ilwis.do('setvaluerange', Greens, 0, 255, 1)
print()
print(minPerc1)
print(maxPerc1)
stat_Red = Red.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_Red.calcStretchRange(1)
Reds = ilwis.do('linearstretch',Red, minPerc1, maxPerc1)
Reds = ilwis.do('setvaluerange', Reds, 0, 255, 1)
print()
print(minPerc1)
print(maxPerc1)
stat_IR = IR.statistics(ilwis.PropertySets.pHISTOGRAM, 65535)
minPerc1, maxPerc1 = stat_IR.calcStretchRange(1)
IRs = ilwis.do('linearstretch',IR, minPerc1, maxPerc1)
IRs = ilwis.do('setvaluerange', IRs, 0, 255, 1)
print()
print(minPerc1)
print(maxPerc1)

For visualization in Matplotlib (using Imshow) the data is transformed into a numpy array, using the ILWISPY operation 'iter', each pixel is assigned into a 1 D array, which by numpy is reshaped back into a 2-D array - for each of the spectral channels

In [ ]:
stats_IRs = IRs.statistics(ilwis.PropertySets.pHISTOGRAM)
print(stats_IRs.histogram())

In [ ]:
#Transform to a numpy array for visualization using imshow
row = IRs.size().ysize 
col = IRs.size().xsize
dim = IRs.size().linearSize()
print(row, col, dim)

Blues_2np = np.fromiter(iter(Blues), np.ubyte, dim) 
Blues_2np = Blues_2np.reshape((row, col))

Greens_2np = np.fromiter(iter(Greens), np.ubyte, dim) 
Greens_2np = Greens_2np.reshape((row, col))

Reds_2np = np.fromiter(iter(Reds), np.ubyte, dim) 
Reds_2np = Reds_2np.reshape((row, col))

IRs_2np = np.fromiter(iter(IRs), np.ubyte, dim) 
IRs_2np = IRs_2np.reshape((row, col))

A numpy multi dimensional data stack is created, for visualization in Matplotlib the data is organized  pixel interleaved, to use the results later as an ILWIS Maplist, the data stack is transformed into a multi-dimensional array which is band interleaved

In [ ]:
# create  color composite (in RGB)
#pixel interleaved
fc_S2 = np.dstack((IRs_2np, Reds_2np, Greens_2np))
nc_S2 = np.dstack((Reds_2np, Greens_2np, Blues_2np))

#band interleaved
S2ALL = np.array([Blues_2np, Greens_2np, Reds_2np, IRs_2np])

Create a RGB plot showing a true color composite as well as a false colour composite

In [ ]:
fig1 = plt.figure(figsize=(15, 10))
plt.subplot(1, 2, 1)
plt.imshow(nc_S2)
plt.title('NC - S2 image retrieved from DataSpace.Copernicus.EU')
plt.subplot(1, 2, 2)
plt.imshow(fc_S2)
plt.title('FC - S2 image retrieved from DataSpace.Copernicus.EU');

Export results as a new ILWIS image
Create a new  / empty image and as second step load the data and write the output to disk. Review your results using ILWIS386

In [ ]:
#create empty ilwis raster 
S2_Enschede = ilwis.RasterCoverage()
defNumr = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0, 255, 1))
S2_Enschede.setDataDef(defNumr)
S2_Enschede.setSize(ilwis.Size(624, 571, 4))
S2_Enschede.setGeoReference(raster.geoReference())

Read the numpy array into the newly created ilwis raster and write the result to disk as an ILWIS maplist, to be further visualized using ILWIS386

In [ ]:
S2_Enschede.array2raster(S2ALL.flatten())
S2_Enschede.store('S2_Enschede.mpl')